In [1]:
import re
import json
from collections import Counter
from importlib.resources import contents

import pandas as pd
import pymysql
import re
from ekonlpy.tag import Mecab
from scipy.special import result

ImportError: cannot import name 'result' from 'scipy.special' (/Users/choihj/paper_project_1/korean-nlp-for-monetary-policy/venv/lib/python3.11/site-packages/scipy/special/__init__.py)

In [2]:
#문장분리기
def sen_split(text):
    return re.split(r'(?<!\w\.\w.)(?<![A-Z][a-z]\.)(?<=\.|\?|\!)\s', str(text))

In [3]:
#정규 표현식으로 필요없는 부분 제거
def tokenize_korean_text(text):
    patterns = [
        r'([a-zA-Z0-9_.+-]+@[a-zA-Z0-9-]+\.[a-zA-Z0-9-.]+)',  # E-mail
        r'(http|ftp|https)://(?:[-\w.]|(?:%[\da-fA-F]{2}))+',  # URL
        r'<[^>]*>',  # HTML tags
        r'([ㄱ-ㅎㅏ-ㅣ]+)',  # Korean consonants and vowels
        r'([가-힣A-Za-z·\d~\-\.]{2,}(로|길)+)',  # Address patterns
        r'([가-힣A-Za-z·\d~\-\.]+(읍|동|번지|시|구)+)',
        r'([가-힣A-Za-z]+(구)\s*[가-힣A-Za-z]+(동))',
        r'([가-힣a-zA-Z\d]+(아파트|빌라|빌딩|마을))',
        r'\n',  # 줄바꿈 제거
        r'[`~!@#$%^&*()_|+\-=?;:,.<>\{\}\[\]\\\/]',  # Special characters
        r'[0-9]'  # Numbers
        r'[^a-zA-Z0-9가-힣]' # 특수문자
    ]
    
    for pattern in patterns:
        text = re.sub(pattern, "", text)
    return text

In [4]:
#각 문서에 대해 문장 분리 및 정규표현식 진행
def start_split_sentences(text):
    sentences = sen_split(text)
    return [tokenize_korean_text(sentence) for sentence in sentences]

In [5]:
df = pd.read_csv("Result_5.csv", header=None, names=["id", "document_type", "date", "title", "media", "sentences", "sentiment_score_market", "reg_date", "content_text"])
df["content_text"] = df["content_text"].apply(json.loads)
df["sentences"] = df["sentences"].apply(json.loads)
df.dtypes

id                         int64
document_type             object
date                      object
title                     object
media                     object
sentences                 object
sentiment_score_market     int64
reg_date                  object
content_text              object
dtype: object

In [29]:
df.head(5)

id   document_type                 date              title media  \
0  7734  analyst_report  2008-04-01 00:00:00  대우증권 월간 채권투자 _4월_  대우증권   
1  7732  analyst_report  2008-04-07 00:00:00             시간차 공격  대우증권   
2  7733  analyst_report  2008-04-07 00:00:00            돌아온 박스권  대우증권   
3  7731  analyst_report  2008-04-14 00:00:00      총재의 변신은 무죄다__  대우증권   
4  7730  analyst_report  2008-04-21 00:00:00      항상 열려는 있는 가능성  대우증권   

                                           sentences  sentiment_score_market  \
0  {'keyword': ['2008_04  
¿ù°£Ã¤±ÇÅõÀÚ
Ã¤±Ç½ÃÀåÀ...                       0   
1  {'keyword': ['Fixed Income Weekly 
2008. 4. 7....                       0   
2  {'keyword': ['Fixed Income Weekly 
2008. 4. 7....                       0   
3  {'keyword': [' 
  
 4월 금통위는 정부-한은간 policy mix ...                       0   
4  {'keyword': [' 
  
 경기 전망은 비교적 분명 … 인플레 명분이 시점...                       0   

              reg_date                                       content_text  
0  2024-09-02 00:00:00  [2008_04  \n¿ù°£Ã¤±ÇÅõÀÚ\nÃ¤±Ç½ÃÀåÀü¸Á\n±ÝÀ¶½Ã...  
1  2024-09-02 00:00:00  [Fixed Income Weekly \n2008. 4. 7.  #918 \nFix...  
2  2024-09-02 00:00:00  [Fixed Income Weekly \n2008. 4. 7.  #918 \nFix...  
3  2024-09-02 00:00:00  [ \n  \n 4월 금통위는 정부-한은간 policy mix 합의의 반영일 수도 ...  
4  2024-09-02 00:00:00  [ \n  \n 경기 전망은 비교적 분명 … 인플레 명분이 시점 결정할 것 \n현 ...

In [6]:
contents=[]
for i in range(len(df['content_text'])):
    contents.append(start_split_sentences(df['content_text'][i]))
contents

[["'20080 n¿ù°£Ã¤±ÇÅõÀÚnÃ¤±Ç½ÃÀåÀü¸Án±ÝÀ¶½ÃÀåÂ÷Æ®ºÏnÓßëë°úùÚÍ£' '월간채권투자  4월 n n對應과 限界 n미국에서는 여전히 연준은 물론 정부와 의회  신용경색 해소를 위해 다방면의 노력을 하고 있다",
  'n하지만 그것은 미 스템의 붕괴는 모면케 해 줄 수 있을지언정 순환적 경기침체까지 피해가게 만들 수는 없을 것 같다',
  '장의 성이 보강되는 가운데에서도 실물경기는  가는 상황이라면 이는 국내 금리에도 하락 여건일 수 있다고 본다',
  ' n이미 정책이 진행중인 미국과 달리 국내에서는 향후 정책의 방향성을 놓고 당국간 입장차가 확연히 n드러나고 있는 상황이다',
  '4월 금통위에서도 그다지 금리 우호적 발언이 나오지 않을 리스크를 경계하고 있는데 하지만 시장 충격이 그다지 크지는 않을  보고 있다',
  ' 관건은 객관적 환경이 에게 유리하게 전개되느냐에 있을 것이기 때문이다',
  '물론 우리는 여전히 시간은 점차 한은 편이 아닐 가능성이 우세하다고 보고 있다',
  'n           n이머징 신용위험 약간 둔화되는 가운데 한국 외화 조달 비용 다소 낮아져 n   n자료 Bloomberg n  n서철수 02768350 n윤여삼 02768402 n윤일광 02768305 n nContent n對應과 限界 n1',
  '동향 n2',
  '채권투자환경 3',
  "요약과 전망 장 차트북1n국내금리 동향 국내금리 주요 스프레드 채권수급 n– 장 n채권수급 – 장 벌 금리 동향 상품 지표  환율 주식 시장  산 시장 리스크  인플레 지표 자금 시장 동향 통화량 지표  기술적 지표 이슈 n25283134374043464952n07070707107107108082120n160200240n280n320CRS3년좌nEMBI 스프레드축반전우bp ' '월간채권투자  4월 n n n1",
  '동향 n강세 흐름 자체는 유지되었으나 환율 및 정책 리스크 부각되며 금리 성 심화 n3월은 전반적인 금리 레벨이 높아진 가

In [7]:
#문장에서 명사만 추출
def extract_nouns_from_sentences(contents):
    mecab = Mecab()
    res = []
    stopwords = ['NNG','NNP','VAX','VV','VCN']  #일반 명사(NNG), 고유 명사(NNP)만 추출

    for text in contents:  #contents는 문장의 리스트 ([[문장1], [문장2], ...])
        tokens = mecab.pos(text)  #형태소 분석
        tokens = mecab.replace_synonyms(tokens)  #동의어 치환
        tokens = mecab.lemmatize(tokens)  #원형 복원
        
        print(tokens)
        
        # 명사만 추출
        nouns = [t_0 for t_0, t_1, *_ in tokens if t_1 in stopwords]
        res.append(nouns)  # 문장별로 명사만 추출하여 결과 리스트에 추가

    return res


In [8]:
res=[]
for i in range(10):
    res.append(extract_nouns_from_sentences(contents[i]))
res

[("'", 'SY'), ('20080', 'SN'), ('n', 'SL'), ('¿', 'SY'), ('ù', 'SL'), ('°£', 'SY'), ('Ã', 'SL'), ('¤±', 'SY'), ('ÇÅõÀÚnÃ', 'SL'), ('¤±', 'SY'), ('Ç', 'SL'), ('½', 'SY'), ('ÃÀåÀü', 'SL'), ('¸', 'SY'), ('Án', 'SL'), ('±', 'SY'), ('ÝÀ', 'SL'), ('¶½', 'SY'), ('ÃÀåÂ÷Æ', 'SL'), ('®º', 'SY'), ('ÏnÓßëë', 'SL'), ('°', 'SY'), ('úùÚÍ', 'SL'), ("£'", 'SY'), ("'", 'SY'), ('월간', 'NNG'), ('채권투자', 'NNG'), ('4', 'SN'), ('월', 'NNBC'), ('n', 'SL'), ('n', 'SL'), ('對應', 'NNG'), ('과', 'JC'), ('限界', 'NNG'), ('n', 'SL'), ('미국', 'NNG'), ('에서', 'JKB'), ('는', 'JX'), ('여전히', 'MAG'), ('fed', 'NNG'), ('은', 'JX'), ('물론', 'MAG'), ('정부', 'NNG'), ('와', 'JC'), ('의회', 'NNG'), ('신용경색', 'NNG'), ('해소', 'NNG'), ('를', 'JKO'), ('위하', 'VV'), ('다방면', 'NNG'), ('의', 'JKG'), ('노력', 'NNG'), ('을', 'JKO'), ('하', 'VV'), ('고', 'EC'), ('있', 'VX'), ('다', 'EC')]
[('n', 'SL'), ('하', 'XSV'), ('지만', 'EC'), ('그것', 'NP'), ('은', 'JX'), ('미', 'NNG'), ('스템', 'NNP'), ('의', 'JKG'), ('붕괴', 'NNG'), ('는', 'JX'), ('모면', 'NNG'), ('케', 'XSV'), ('해', 'VV')

[[['월간',
   '채권투자',
   '對應',
   '限界',
   '미국',
   'fed',
   '정부',
   '의회',
   '신용경색',
   '해소',
   '위하',
   '다방면',
   '노력',
   '하'],
  ['미', '스템', '붕괴', '모면', '해', '있', '순환적', '경기', '침체', '피하', '만들'],
  ['장의',
   '보강',
   '가운데',
   '실물',
   '경기',
   '가',
   '상황',
   '라면',
   '국내',
   '금리',
   '하락',
   '여건',
   '일',
   '있',
   '보'],
  ['정책', '진행', '중', '미국', '국내', '정책', '방향', '놓', '당국', '입장차', '드러나', '상황'],
  ['금통위', '금리', '우호적', '발언', '나오', '위험', '경계', '하', '시장', '충격', '않', '보'],
  ['관건', '객관', '환경', '유리', '전개', '있'],
  ['시간', '한은', '편', '아니', '가능성', '우세'],
  ['신흥국',
   '신용위험',
   '둔화',
   '가운데',
   '한국',
   '외화',
   '조달',
   '비용',
   '자료',
   '서철수',
   '윤여',
   '윤일광',
   '對應',
   '限界'],
  ['동향'],
  ['채권투자', '환경'],
  ['요약',
   '전망',
   '장',
   '차트',
   '북',
   '국내',
   '금리',
   '동향',
   '국내',
   '금리',
   '주요',
   '스프레드',
   '채권',
   '수급',
   '장',
   '채권',
   '수급장',
   '벌',
   '금리',
   '동향',
   '상품',
   '지표',
   '환율',
   '주식시장',
   '산',
   '시장리스크',
   '인플레이션',
   '지표',
   '자금시장',
   '동향'

In [22]:
def remove_stopwords(tokens, stop_words=None):
    if stop_words is None:
        stop_words = ['층', '늘', '년', '후', '장', '리라', 'n', '마산', '가', '를', '을', '점', '관', '월', '일', '텔', '남', '좌', '리', '중', '정', '미', '종']
    
    # 각 문장(sentence)의 각 단어(word)에 대해 불용어 제거
    return [[word for word in sentence if word not in stop_words]for sentence in tokens]


In [23]:
all_tokens = remove_stopwords(res)

In [35]:
from nltk import ngrams

def generate_ngrams(tokens, n):
    return list(ngrams(tokens, n))

n=2
ngram_model=generate_ngrams(all_tokens[0][0], n)
ngram_model

[('월간', '채권투자'),
 ('채권투자', '對應'),
 ('對應', '限界'),
 ('限界', '미국'),
 ('미국', 'fed'),
 ('fed', '정부'),
 ('정부', '의회'),
 ('의회', '신용경색'),
 ('신용경색', '해소'),
 ('해소', '위하'),
 ('위하', '다방면'),
 ('다방면', '노력'),
 ('노력', '하')]